In [1]:
import os
import sys
sys.path.append(os.getcwd())
sys.path.append(os.getcwd() + '/../src')

In [2]:
import pickle
import numpy as np
import matplotlib.pyplot as plt
from collections import defaultdict
import os
import wandb
from concurrent.futures import ThreadPoolExecutor
import multiprocessing
import logging
import sys
from recurrent.parameters import AllLogs

import jax 
import jax.numpy as jnp
jax.config.update("jax_platform_name", "cpu")


In [3]:
# Configure logging
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s',
    handlers=[
        logging.StreamHandler(sys.stdout),
        logging.FileHandler('processing.log')
    ]
)
logger = logging.getLogger(__name__)

# Set multiprocessing start method to 'spawn' to avoid JAX fork issues
multiprocessing.set_start_method("spawn", force=True)

In [4]:
# Configuration
download_dir = "/scratch/downloaded_artifacts"
results_dir = "/scratch/results"
entity = "wlp9800-new-york-university"
project_name = "oho_exps"
group_name = "mlr_search-1_aa9c06652fb34624bebe972b1fe7292f"
max_download_workers = 20
max_process_workers = 10  # Reduced for ThreadPoolExecutor stability

# Ensure download directory exists
os.makedirs(download_dir, exist_ok=True)

In [18]:
# Function to download a single run's artifact
def download_artifact(run_data):
    run_id = run_data["id"]
    config = run_data["config"]
    try:
        api = wandb.Api()
        artifact = api.artifact(f'{entity}/{project_name}/logs_{run_id}:v0')
        artifact_dir = os.path.join(download_dir, artifact.name)
        artifact.download(root=artifact_dir)
        logger.info(f"Downloaded {artifact.name} to {artifact_dir}")
        return {
            "run_id": run_id,
            "artifact_dir": artifact_dir,
            "config": config,
            "status": "success"
        }
    except Exception as e:
        logger.error(f"Error downloading artifact for run {run_id}: {str(e)}")
        return {
            "run_id": run_id,
            "artifact_dir": None,
            "config": config,
            "status": f"error: {str(e)}"
        }
    
# New import
import re

# New function to sanitize folder names
def sanitize_folder_name(name):
    return re.sub(r'[^\w\-]', '_', str(name))

# Function to process a single run's logs
def process_run(run_result):
    run_id = run_result["run_id"]
    artifact_dir = run_result["artifact_dir"]
    config = run_result["config"]
    
    if run_result["status"] != "success" or not artifact_dir or not config:
        logger.warning(f"Skipping run {run_id}: download failed or no config")
        return {
            "run_id": run_id,
            "status": "skipped",
            "data": None
        }
    
    log_file = os.path.join(artifact_dir, "logs.pkl")
    if not os.path.exists(log_file):
        logger.error(f"Logs file not found for run {run_id}")
        return {
            "run_id": run_id,
            "status": "no_log_file",
            "data": None
        }
    
    try:
        with open(log_file, "rb") as f:
            logs = pickle.load(f)
        
        if not isinstance(logs, AllLogs):
            logger.error(f"Logs for run {run_id} is not an AllLogs instance")
            return {
                "run_id": run_id,
                "status": "invalid_logs",
                "data": None
            }
        
        ts = tuple(config.get("ts", ()))
        outer_lr = config.get("outer_learning_rate")
        inner_lr = config.get("inner_learning_rate")
        inner_learner = config.get("inner_learner", "unknown")
        inner_learner = [inner_learner] if not isinstance(inner_learner, list) else inner_learner
        
        if outer_lr is None or inner_lr is None or not ts:
            logger.error(f"Missing config values for run {run_id}")
            return {
                "run_id": run_id,
                "status": "missing_config",
                "data": None
            }
        
        is_success = not np.any(logs.hyperparameters == 1e-4)
        logger.info(f"Processed run {run_id}: success={is_success}")
        
        return {
            "run_id": run_id,
            "status": "success",
            "data": {
                "ts": ts,
                "outer_lr": outer_lr,
                "inner_lr": inner_lr,
                "inner_learner": inner_learner,
                "is_success": is_success
            }
        }
    except Exception as e:
        logger.error(f"Error processing logs for run {run_id}: {str(e)}")
        return {
            "run_id": run_id,
            "status": f"error: {str(e)}",
            "data": None
        }

In [19]:
def create_heatmap(ts, runs_data, group_idx, group_name, subfolder=None, inner_learner=None):
    if inner_learner:
        runs_data = [run for run in runs_data if inner_learner in run["inner_learner"]]
    outer_lrs = sorted(set(run["outer_lr"] for run in runs_data))
    inner_lrs = sorted(set(run["inner_lr"] for run in runs_data))
    
    if not outer_lrs or not inner_lrs:
        logger.warning(f"No valid learning rates for ts group {ts} in {group_name}{f'/{subfolder}' if subfolder else ''}{f' (inner_learner={inner_learner})' if inner_learner else ''}")
        return
    
    grid = np.zeros((len(inner_lrs), len(outer_lrs)))
    success_counts = defaultdict(int)
    total_counts = defaultdict(int)
    
    for run in runs_data:
        outer_idx = outer_lrs.index(run["outer_lr"])
        inner_idx = inner_lrs.index(run["inner_lr"])
        key = (inner_idx, outer_idx)
        total_counts[key] += 1
        if run["is_success"]:
            success_counts[key] += 1
    
    for (inner_idx, outer_idx), total in total_counts.items():
        successes = success_counts.get((inner_idx, outer_idx), 0)
        grid[inner_idx, outer_idx] = successes / total if total > 0 else 0
    
    plt.figure(figsize=(12, 10))
    im = plt.imshow(grid, origin='lower', cmap='viridis', interpolation='nearest')
    plt.colorbar(im, label='Fraction of Successful Runs')
    
    for i in range(len(inner_lrs)):
        for j in range(len(outer_lrs)):
            fraction = grid[i, j]
            text = f"{fraction:.2f}" if total_counts.get((i, j), 0) > 0 else "N/A"
            plt.text(j, i, text, ha='center', va='center', color='white' if fraction < 0.5 else 'black')
    
    plt.xticks(np.arange(len(outer_lrs)), [f"{lr:.1e}" for lr in outer_lrs], rotation=45)
    plt.yticks(np.arange(len(inner_lrs)), [f"{lr:.1e}" for lr in inner_lrs])
    plt.xlabel('Outer Learning Rate')
    plt.ylabel('Inner Learning Rate')
    title = f'Success Fraction Heatmap for ts={ts} in {group_name}'
    if subfolder:
        title += f' ({subfolder})'
    if inner_learner:
        title += f' (inner_learner={inner_learner})'
    plt.title(title)
    
    group_results_dir = os.path.join(results_dir, group_name, subfolder or '')
    os.makedirs(group_results_dir, exist_ok=True)
    output_file = os.path.join(group_results_dir, f'heatmap_ts_group_{group_idx}.png')
    plt.savefig(output_file, bbox_inches='tight')
    plt.close()
    logger.info(f"Saved heatmap for ts={ts} in {group_name}{f'/{subfolder}' if subfolder else ''}{f' (inner_learner={inner_learner})' if inner_learner else ''} to {output_file}")

# Modified create_aggregated_heatmap (updated to handle inner_learner filtering)
def create_aggregated_heatmap(all_runs_data, group_name, subfolder=None, inner_learner=None):
    if inner_learner:
        all_runs_data = [run for run in all_runs_data if inner_learner in run["inner_learner"]]
    outer_lrs = sorted(set(run["outer_lr"] for run in all_runs_data))
    inner_lrs = sorted(set(run["inner_lr"] for run in all_runs_data))
    
    if not outer_lrs or not inner_lrs:
        logger.warning(f"No valid learning rates for aggregated heatmap in {group_name}{f'/{subfolder}' if subfolder else ''}{f' (inner_learner={inner_learner})' if inner_learner else ''}")
        return
    
    grid = np.zeros((len(inner_lrs), len(outer_lrs)))
    success_counts = defaultdict(int)
    total_counts = defaultdict(int)
    
    for run in all_runs_data:
        outer_idx = outer_lrs.index(run["outer_lr"])
        inner_idx = inner_lrs.index(run["inner_lr"])
        key = (inner_idx, outer_idx)
        total_counts[key] += 1
        if run["is_success"]:
            success_counts[key] += 1
    
    for (inner_idx, outer_idx), total in total_counts.items():
        successes = success_counts.get((inner_idx, outer_idx), 0)
        grid[inner_idx, outer_idx] = successes / total if total > 0 else 0
    
    plt.figure(figsize=(12, 10))
    im = plt.imshow(grid, origin='lower', cmap='viridis', interpolation='nearest')
    plt.colorbar(im, label='Fraction of Successful Runs')
    
    for i in range(len(inner_lrs)):
        for j in range(len(outer_lrs)):
            fraction = grid[i, j]
            text = f"{fraction:.2f}" if total_counts.get((i, j), 0) > 0 else "N/A"
            plt.text(j, i, text, ha='center', va='center', color='white' if fraction < 0.5 else 'black')
    
    plt.xticks(np.arange(len(outer_lrs)), [f"{lr:.1e}" for lr in outer_lrs], rotation=45)
    plt.yticks(np.arange(len(inner_lrs)), [f"{lr:.1e}" for lr in inner_lrs])
    plt.xlabel('Outer Learning Rate')
    plt.ylabel('Inner Learning Rate')
    title = f'Aggregated Success Fraction Heatmap in {group_name}'
    if subfolder:
        title += f' ({subfolder})'
    if inner_learner:
        title += f' (inner_learner={inner_learner})'
    plt.title(title)
    
    group_results_dir = os.path.join(results_dir, group_name, subfolder or '')
    os.makedirs(group_results_dir, exist_ok=True)
    output_file = os.path.join(group_results_dir, 'heatmap_aggregated.png')
    plt.savefig(output_file, bbox_inches='tight')
    plt.close()
    logger.info(f"Saved aggregated heatmap in {group_name}{f'/{subfolder}' if subfolder else ''}{f' (inner_learner={inner_learner})' if inner_learner else ''} to {output_file}")

In [7]:
api = wandb.Api()
runs = api.runs(
    path=f"{entity}/{project_name}",
    filters={"group": group_name}
)

# Prepare run data
run_data = [{"id": run.id, "config": run.config} for run in runs]
logger.info(f"Found {len(run_data)} runs to process")

wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.
wandb: Network error (HTTPError), entering retry loop.


2025-04-19 00:26:59,456 - INFO - Found 10800 runs to process


In [8]:
with ThreadPoolExecutor(max_workers=max_download_workers) as executor:
    download_results = list(executor.map(download_artifact, run_data))

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb:   1 of 1 files downloaded.  


2025-04-19 00:27:03,672 - INFO - Downloaded logs_isv73zvp:v0 to /scratch/downloaded_artifacts/logs_isv73zvp:v0


wandb:   1 of 1 files downloaded.  
wandb:   1 of 1 files downloaded.  


2025-04-19 00:27:03,912 - INFO - Downloaded logs_1nr7lnlj:v0 to /scratch/downloaded_artifacts/logs_1nr7lnlj:v0


wandb:   1 of 1 files downloaded.  


...

2025-04-19 00:51:20,315 - INFO - Downloaded logs_1ok6vdyk:v0 to /scratch/downloaded_artifacts/logs_1ok6vdyk:v0


wandb:   1 of 1 files downloaded.  


2025-04-19 00:51:20,422 - INFO - Downloaded logs_fuwg3o1y:v0 to /scratch/downloaded_artifacts/logs_fuwg3o1y:v0


wandb:   1 of 1 files downloaded.  


2025-04-19 00:51:20,457 - INFO - Downloaded logs_tpszpd3f:v0 to /scratch/downloaded_artifacts/logs_tpszpd3f:v0


In [9]:
with ThreadPoolExecutor(max_workers=max_process_workers) as executor:
    process_results = list(executor.map(process_run, download_results))

INFO:2025-04-19 00:51:25,215:jax._src.xla_bridge:925: Unable to initialize backend 'rocm': module 'jaxlib.xla_extension' has no attribute 'GpuAllocatorConfig'


2025-04-19 00:51:25,215 - INFO - Unable to initialize backend 'rocm': module 'jaxlib.xla_extension' has no attribute 'GpuAllocatorConfig'


INFO:2025-04-19 00:51:25,241:jax._src.xla_bridge:925: Unable to initialize backend 'tpu': INTERNAL: Failed to open libtpu.so: libtpu.so: cannot open shared object file: No such file or directory


2025-04-19 00:51:25,241 - INFO - Unable to initialize backend 'tpu': INTERNAL: Failed to open libtpu.so: libtpu.so: cannot open shared object file: No such file or directory
2025-04-19 00:51:26,408 - INFO - Processed run 79ygnuzq: success=True
2025-04-19 00:51:26,409 - INFO - Processed run 0lfnlsx6: success=True
2025-04-19 00:51:26,409 - INFO - Processed run e0fh6y0e: success=False
2025-04-19 00:51:26,409 - INFO - Processed run 1nr7lnlj: success=True
2025-04-19 00:51:26,409 - INFO - Processed run g1mnjrxk: success=True
2025-04-19 00:51:26,410 - INFO - Processed run 9ob4c701: success=False
2025-04-19 00:51:26,410 - INFO - Processed run gvfaz9pa: success=True
2025-04-19 00:51:26,410 - INFO - Processed run di860t9p: success=True
2025-04-19 00:51:26,410 - INFO - Processed run abwe9znm: success=True
2025-04-19 00:51:26,410 - INFO - Processed run 7u6yxcmw: success=True
2025-04-19 00:51:26,545 - INFO - Processed run mu7o9913: success=True
2025-04-19 00:51:26,677 - INFO - Processed run vpwxx9o

In [14]:
all_runs_data = []
run_groups = defaultdict(list)
for result in process_results:
    if result["status"] == "success" and result["data"]:
        run_groups[result["data"]["ts"]].append(result["data"])
        all_runs_data.append(result["data"])

In [15]:

for idx, (ts, runs_data) in enumerate(run_groups.items()):
    logger.info(f"Generating heatmap for ts group {ts} in {group_name}")
    create_heatmap(ts, runs_data, idx, group_name)

2025-04-19 01:04:09,269 - INFO - Generating heatmap for ts group (0, 2) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f
2025-04-19 01:04:09,507 - INFO - Saved heatmap for ts=(0, 2) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f to /scratch/results/mlr_search-1_aa9c06652fb34624bebe972b1fe7292f/heatmap_ts_group_0.png
2025-04-19 01:04:09,508 - INFO - Generating heatmap for ts group (1, 3) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f
2025-04-19 01:04:09,742 - INFO - Saved heatmap for ts=(1, 3) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f to /scratch/results/mlr_search-1_aa9c06652fb34624bebe972b1fe7292f/heatmap_ts_group_1.png
2025-04-19 01:04:09,743 - INFO - Generating heatmap for ts group (2, 4) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f
2025-04-19 01:04:09,988 - INFO - Saved heatmap for ts=(2, 4) in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f to /scratch/results/mlr_search-1_aa9c06652fb34624bebe972b1fe7292f/heatmap_ts_group_2.png
2025-04-19 01:04:09,989 - INFO - Generat

In [16]:
def create_aggregated_heatmap(all_runs_data, group_name, subfolder=None):
    outer_lrs = sorted(set(run["outer_lr"] for run in all_runs_data))
    inner_lrs = sorted(set(run["inner_lr"] for run in all_runs_data))
    
    if not outer_lrs or not inner_lrs:
        logger.warning(f"No valid learning rates for aggregated heatmap in {group_name}{f'/{subfolder}' if subfolder else ''}")
        return
    
    grid = np.zeros((len(inner_lrs), len(outer_lrs)))
    success_counts = defaultdict(int)
    total_counts = defaultdict(int)
    
    for run in all_runs_data:
        outer_idx = outer_lrs.index(run["outer_lr"])
        inner_idx = inner_lrs.index(run["inner_lr"])
        key = (inner_idx, outer_idx)
        total_counts[key] += 1
        if run["is_success"]:
            success_counts[key] += 1
    
    for (inner_idx, outer_idx), total in total_counts.items():
        successes = success_counts.get((inner_idx, outer_idx), 0)
        grid[inner_idx, outer_idx] = successes / total if total > 0 else 0
    
    plt.figure(figsize=(12, 10))
    im = plt.imshow(grid, origin='lower', cmap='viridis', interpolation='nearest')
    plt.colorbar(im, label='Fraction of Successful Runs')
    
    for i in range(len(inner_lrs)):
        for j in range(len(outer_lrs)):
            fraction = grid[i, j]
            text = f"{fraction:.2f}" if total_counts.get((i, j), 0) > 0 else "N/A"
            plt.text(j, i, text, ha='center', va='center', color='white' if fraction < 0.5 else 'black')
    
    plt.xticks(np.arange(len(outer_lrs)), [f"{lr:.1e}" for lr in outer_lrs], rotation=45)
    plt.yticks(np.arange(len(inner_lrs)), [f"{lr:.1e}" for lr in inner_lrs])
    plt.xlabel('Outer Learning Rate')
    plt.ylabel('Inner Learning Rate')
    plt.title(f'Aggregated Success Fraction Heatmap in {group_name}{f" ({subfolder})" if subfolder else ""}')
    
    group_results_dir = os.path.join(results_dir, group_name, subfolder or '')
    os.makedirs(group_results_dir, exist_ok=True)
    output_file = os.path.join(group_results_dir, 'heatmap_aggregated.png')
    plt.savefig(output_file, bbox_inches='tight')
    plt.close()
    logger.info(f"Saved aggregated heatmap in {group_name}{f'/{subfolder}' if subfolder else ''} to {output_file}")

In [17]:
# Generate aggregated heatmap
logger.info(f"Generating aggregated heatmap in {group_name}")
create_aggregated_heatmap(all_runs_data, group_name)

2025-04-19 01:04:21,993 - INFO - Generating aggregated heatmap in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f
2025-04-19 01:04:22,261 - INFO - Saved aggregated heatmap in mlr_search-1_aa9c06652fb34624bebe972b1fe7292f to /scratch/results/mlr_search-1_aa9c06652fb34624bebe972b1fe7292f/heatmap_aggregated.png
